# <center>TEXT DATA PREPROCESSING </center>

### IMPORT LIBRARIES

In [27]:
import numpy as np
import pandas as pd 
import nltk
from sklearn.preprocessing import OneHotEncoder
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
from collections import OrderedDict, defaultdict
from collections import Counter

install and inport necessary packages

In [7]:
for resource in ['punkt', 'punkt_tab', 'stopwords', 'wordnet', 'averaged_perceptron_tagger', 'averaged_perceptron_tagger_eng']:
    try:
        nltk.data.find(f'tokenizers/{resource}')
    except LookupError:
        nltk.download(resource)


from nltk.tokenize import sent_tokenize, word_tokenize
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from nltk.corpus import wordnet
from nltk.stem import PorterStemmer

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\ADMIN\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\ADMIN\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     C:\Users\ADMIN\AppData\Roaming\nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package averaged_perceptron_tagger_eng to
[nltk_data]     C:\Users\ADMIN\AppData\Roaming\nltk_data...
[nltk_data]   Package averaged_perceptron_tagger_eng is already up-to-
[nltk_data]       date!


### LOAD DATASET

In [8]:
data = pd.read_csv("../data/IMDB Dataset.csv")  # Load the dataset
reviews = data['review'].values  # Extract reviews from the dataset
labels = data['sentiment'].values  # Extract sentiment labels from the dataset
data.head() # Display the first few rows of the dataset

review sentiment
0  One of the other reviewers has mentioned that ...  positive
1  A wonderful little production. <br /><br />The...  positive
2  I thought this was a wonderful way to spend ti...  positive
3  Basically there's a family where a little boy ...  negative
4  Petter Mattei's "Love in the Time of Money" is...  positive

### TOKENIZATION

Sentence Tokenization

In [9]:
sentences = []
for review in reviews:
    sentences.append(sent_tokenize(review))  # Sentence tokenization

In [10]:
print(sentences[0]) # Print the first review after sentence tokenization

["One of the other reviewers has mentioned that after watching just 1 Oz episode you'll be hooked.", 'They are right, as this is exactly what happened with me.<br /><br />The first thing that struck me about Oz was its brutality and unflinching scenes of violence, which set in right from the word GO.', 'Trust me, this is not a show for the faint hearted or timid.', 'This show pulls no punches with regards to drugs, sex or violence.', 'Its is hardcore, in the classic use of the word.<br /><br />It is called OZ as that is the nickname given to the Oswald Maximum Security State Penitentary.', 'It focuses mainly on Emerald City, an experimental section of the prison where all the cells have glass fronts and face inwards, so privacy is not high on the agenda.', "Em City is home to many..Aryans, Muslims, gangstas, Latinos, Christians, Italians, Irish and more....so scuffles, death stares, dodgy dealings and shady agreements are never far away.<br /><br />I would say the main appeal of the sh

Word Tokenization

In [11]:
words = []
for review in reviews:
    words.append(word_tokenize(review))  # Word tokenization

In [12]:
print(words[0])  # Print the first review after word tokenization

['One', 'of', 'the', 'other', 'reviewers', 'has', 'mentioned', 'that', 'after', 'watching', 'just', '1', 'Oz', 'episode', 'you', "'ll", 'be', 'hooked', '.', 'They', 'are', 'right', ',', 'as', 'this', 'is', 'exactly', 'what', 'happened', 'with', 'me.', '<', 'br', '/', '>', '<', 'br', '/', '>', 'The', 'first', 'thing', 'that', 'struck', 'me', 'about', 'Oz', 'was', 'its', 'brutality', 'and', 'unflinching', 'scenes', 'of', 'violence', ',', 'which', 'set', 'in', 'right', 'from', 'the', 'word', 'GO', '.', 'Trust', 'me', ',', 'this', 'is', 'not', 'a', 'show', 'for', 'the', 'faint', 'hearted', 'or', 'timid', '.', 'This', 'show', 'pulls', 'no', 'punches', 'with', 'regards', 'to', 'drugs', ',', 'sex', 'or', 'violence', '.', 'Its', 'is', 'hardcore', ',', 'in', 'the', 'classic', 'use', 'of', 'the', 'word.', '<', 'br', '/', '>', '<', 'br', '/', '>', 'It', 'is', 'called', 'OZ', 'as', 'that', 'is', 'the', 'nickname', 'given', 'to', 'the', 'Oswald', 'Maximum', 'Security', 'State', 'Penitentary', '.', 

Subword Tokenization using byte-pair encoding

Define function to be used

In [28]:
def create_char_vocabulary(review): # Function to create character-level vocabulary and their counts
    
    char_vocab = defaultdict(int)
    
    for token in review:
        # Convert each word to space-separated characters
        char_sequence = ' '.join(list(token))
        char_vocab[char_sequence] += 1
    
    return OrderedDict(sorted(char_vocab.items(), key=lambda x: x[1], reverse=True))

def get_pairs(vocab): # Function to get pairs of adjacent symbols in the vocabulary
    pairs = Counter()
    for word, freq in vocab.items():
        symbols = word.split()
        for i in range(len(symbols)-1):
            pairs[(symbols[i], symbols[i+1])] += freq
    return pairs

def merge_vocab(vocab, pair):   # Function to merge the most frequent pair in the vocabulary
    new_vocab = {}
    old = ' '.join(pair)
    new = ''.join(pair)
    for word, freq in vocab.items():
        new_word = word.replace(old, new)
        new_vocab[new_word] = freq
    return new_vocab


Create character vocabulary from the word tokenized review

In [ ]:
char_vocab = defaultdict(int)
for word_tokens in words:
    chars = create_char_vocabulary(word_tokens)
    for char_sequence in chars:
        char_vocab[char_sequence] += 1

ordered_char_vocab = OrderedDict(sorted(char_vocab.items(), key=lambda x: x[1], reverse=True)) # Sort the character vocabulary by frequency

print("Character-level vocabulary (top 10):")
for i, (char_seq, freq) in enumerate(ordered_char_vocab.items()):
    if i < 10:
        print(f"'{char_seq}': {freq}")
    else:
        break

Character-level vocabulary (top 10):
'.': 49329
't h e': 49315
'a': 48073
',': 48052
'a n d': 48044
'o f': 47347
't o': 46880
'i s': 44826
'i n': 43383
't h i s': 42064


In [ ]:
# BPE Merging Process
num_merges = 500
for _ in range(num_merges):
    pairs = get_pairs(char_vocab)
    if not pairs:   # if there is no more pair
        break
    most_common = pairs.most_common(1)[0][0]
    char_vocab = merge_vocab(char_vocab, most_common)
    print(f"Merged: {most_common} -> {''.join(most_common)}")

Merged: ('i', 'n') -> in
Merged: ('e', 'r') -> er
Merged: ('t', 'h') -> th
Merged: ('r', 'e') -> re
Merged: ('e', 'n') -> en
Merged: ('a', 'n') -> an
Merged: ('o', 'n') -> on
Merged: ('in', 'g') -> ing
Merged: ('s', 't') -> st
Merged: ('a', 't') -> at
Merged: ('a', 'l') -> al
Merged: ('o', 'r') -> or
Merged: ('o', 'u') -> ou
Merged: ('e', 's') -> es
Merged: ('e', 'd') -> ed
Merged: ('a', 'r') -> ar
Merged: ('i', 's') -> is
Merged: ('l', 'y') -> ly
Merged: ('i', 't') -> it
Merged: ('l', 'e') -> le
Merged: ('c', 'h') -> ch
Merged: ('s', 'e') -> se
Merged: ('o', 'm') -> om
Merged: ('c', 't') -> ct
Merged: ('a', 's') -> as
Merged: ('i', 'l') -> il
Merged: ('i', 'c') -> ic
Merged: ('b', 'e') -> be
Merged: ('o', 'w') -> ow
Merged: ('v', 'e') -> ve
Merged: ('a', 'd') -> ad
Merged: ('w', 'h') -> wh
Merged: ('o', 't') -> ot
Merged: ('i', 'on') -> ion
Merged: ('h', 'e') -> he
Merged: ('a', 'y') -> ay
Merged: ('l', 'i') -> li
Merged: ('g', 'h') -> gh
Merged: ('t', 'o') -> to
Merged: ('i', 'm') ->

In [24]:
print("\nFinal Vocabulary:")
for word in char_vocab:
    print(word)


Final Vocabulary:
,
t h e
.
i s
o f
<
b r
/
>
a n d
t o
I
w i t h
f o r
t h a t
O z
a s
v i o l e n c e
i t
y o u
' l l
m e
w a s
i n
a
s h o w
o r
o n
p r i s o n
s o
n ' t
o t h e r
j u s t
e p i s o d e
b e
a r e
r i g h t
t h i s
w h a t
T h e
f i r s t
s t r u c k
n o t
I t
O Z
C i t y
w h e r e
h i g h
m o r e
. . . .
w o u l d
s a y
d u e
f o r g e t
b u t
w h o
i n m a t e s
g e t
O n e
r e v i e w e r s
h a s
m e n t i o n e d
a f t e r
w a t c h i n g
1
h o o k e d
T h e y
e x a c t l y
h a p p e n e d
m e .
t h i n g
a b o u t
i t s
b r u t a l i t y
u n f l i n c h i n g
s c e n e s
w h i c h
s e t
f r o m
w o r d
G O
T r u s t
f a i n t
h e a r t e d
t i m i d
T h i s
p u l l s
n o
p u n c h e s
r e g a r d s
d r u g s
s e x
I t s
h a r d c o r e
c l a s s i c
u s e
w o r d .
c a l l e d
n i c k n a m e
g i v e n
O s w a l d
M a x i m u m
S e c u r i t y
S t a t e
P e n i t e n t a r y
f o c u s e s
m a i n l y
E m e r a l d
a n
e x p e r i m e n t a l
s e c t i o n
a l l

### REMOVING STOP WORD

In [ ]:
filtered_words = []
stop_words = set(stopwords.words('english'))  # Define stopwords set
for review_words in words:
    filtered_review = [word for word in review_words if word.lower() not in stop_words] # Filter stopwords for each review
    filtered_words.append(filtered_review) # Append the filtered review to the list

In [37]:
print(filtered_words[0])  # Print the first reviews after word tokenization and stopword removal

['One', 'reviewers', 'mentioned', 'watching', '1', 'Oz', 'episode', "'ll", 'hooked', '.', 'right', ',', 'exactly', 'happened', 'me.', '<', 'br', '/', '>', '<', 'br', '/', '>', 'first', 'thing', 'struck', 'Oz', 'brutality', 'unflinching', 'scenes', 'violence', ',', 'set', 'right', 'word', 'GO', '.', 'Trust', ',', 'show', 'faint', 'hearted', 'timid', '.', 'show', 'pulls', 'punches', 'regards', 'drugs', ',', 'sex', 'violence', '.', 'hardcore', ',', 'classic', 'use', 'word.', '<', 'br', '/', '>', '<', 'br', '/', '>', 'called', 'OZ', 'nickname', 'given', 'Oswald', 'Maximum', 'Security', 'State', 'Penitentary', '.', 'focuses', 'mainly', 'Emerald', 'City', ',', 'experimental', 'section', 'prison', 'cells', 'glass', 'fronts', 'face', 'inwards', ',', 'privacy', 'high', 'agenda', '.', 'Em', 'City', 'home', 'many', '..', 'Aryans', ',', 'Muslims', ',', 'gangstas', ',', 'Latinos', ',', 'Christians', ',', 'Italians', ',', 'Irish', '....', 'scuffles', ',', 'death', 'stares', ',', 'dodgy', 'dealings',

### STEMMING AND LEMMATIZATION

STEMMING

In [46]:
stemmer = PorterStemmer()
stemmed_words = []
for review_words in filtered_words:
    stemmed_review = [stemmer.stem(word) for word in review_words]  # Stemming
    stemmed_words.append(stemmed_review)  # Append the stemmed review to the list

In [47]:
print(stemmed_words[0])  # Print the first reviews after word tokenization, stopword removal, and stemming

['one', 'review', 'mention', 'watch', '1', 'oz', 'episod', "'ll", 'hook', '.', 'right', ',', 'exactli', 'happen', 'me.', '<', 'br', '/', '>', '<', 'br', '/', '>', 'first', 'thing', 'struck', 'oz', 'brutal', 'unflinch', 'scene', 'violenc', ',', 'set', 'right', 'word', 'go', '.', 'trust', ',', 'show', 'faint', 'heart', 'timid', '.', 'show', 'pull', 'punch', 'regard', 'drug', ',', 'sex', 'violenc', '.', 'hardcor', ',', 'classic', 'use', 'word.', '<', 'br', '/', '>', '<', 'br', '/', '>', 'call', 'oz', 'nicknam', 'given', 'oswald', 'maximum', 'secur', 'state', 'penitentari', '.', 'focus', 'mainli', 'emerald', 'citi', ',', 'experiment', 'section', 'prison', 'cell', 'glass', 'front', 'face', 'inward', ',', 'privaci', 'high', 'agenda', '.', 'em', 'citi', 'home', 'mani', '..', 'aryan', ',', 'muslim', ',', 'gangsta', ',', 'latino', ',', 'christian', ',', 'italian', ',', 'irish', '....', 'scuffl', ',', 'death', 'stare', ',', 'dodgi', 'deal', 'shadi', 'agreement', 'never', 'far', 'away.', '<', 'br

 LEMMATIZATION

Define function to be used

In [ ]:
def get_wordnet_pos(word): # Function to map NLTK POS tags to WordNet POS tags
    tag = nltk.pos_tag([word])[0][1][0].upper()
    tag_dict = {"J": wordnet.ADJ, "N": wordnet.NOUN, "V": wordnet.VERB, "R": wordnet.ADV}
    return tag_dict.get(tag, wordnet.NOUN)

In [43]:
lemmatizer = WordNetLemmatizer()
lemmatized_words = []

for review_words in filtered_words:
    lemmatized_review = [lemmatizer.lemmatize(word, get_wordnet_pos(word)) for word in review_words]  # Lemmatization
    lemmatized_words.append(lemmatized_review)  # Append the lemmatized review to the list

In [44]:
print(lemmatized_words[0])  # Print the first reviews after word tokenization, stopword removal, and lemmatization

['One', 'reviewer', 'mention', 'watch', '1', 'Oz', 'episode', "'ll", 'hooked', '.', 'right', ',', 'exactly', 'happen', 'me.', '<', 'br', '/', '>', '<', 'br', '/', '>', 'first', 'thing', 'struck', 'Oz', 'brutality', 'unflinching', 'scene', 'violence', ',', 'set', 'right', 'word', 'GO', '.', 'Trust', ',', 'show', 'faint', 'hearted', 'timid', '.', 'show', 'pull', 'punch', 'regard', 'drug', ',', 'sex', 'violence', '.', 'hardcore', ',', 'classic', 'use', 'word.', '<', 'br', '/', '>', '<', 'br', '/', '>', 'call', 'OZ', 'nickname', 'give', 'Oswald', 'Maximum', 'Security', 'State', 'Penitentary', '.', 'focus', 'mainly', 'Emerald', 'City', ',', 'experimental', 'section', 'prison', 'cell', 'glass', 'front', 'face', 'inwards', ',', 'privacy', 'high', 'agenda', '.', 'Em', 'City', 'home', 'many', '..', 'Aryans', ',', 'Muslims', ',', 'gangsta', ',', 'Latinos', ',', 'Christians', ',', 'Italians', ',', 'Irish', '....', 'scuffle', ',', 'death', 'stare', ',', 'dodgy', 'dealing', 'shady', 'agreement', 'n

### TEXT VECTORIZATION

Cut down the number of vocabulary for vectorizing

In [68]:
word_counts = Counter([w for doc in lemmatized_words for w in doc])
common_words = [w for w, c in word_counts.items() if c >= 5]  # keep words seen ≥5 times
print(f"Total unique words before reduction: {len(word_counts)}")
print(f"Number of common words (appearing at least 5 times): {len(common_words)}")

Total unique words before reduction: 179007
Number of common words (appearing at least 5 times): 43830


One-Hot Encoding

In [69]:
vocabulary = sorted(set(common_words))  # Create a sorted set of unique words from the stemmed words)
encoder = OneHotEncoder(sparse_output=False)
encoded_reviews = encoder.fit_transform(np.array(vocabulary).reshape(-1, 1))  # One-hot encode the stemmed words
word_to_onehot = {vocabulary[i]: encoded_reviews[i]
                  for i in range(len(vocabulary))}

for word, vector in word_to_onehot.items():
    print(f"Word: {word}, One-Hot Encoding: {vector}")

Word: !, One-Hot Encoding: [1. 0. 0. ... 0. 0. 0.]
Word: #, One-Hot Encoding: [0. 1. 0. ... 0. 0. 0.]
Word: $, One-Hot Encoding: [0. 0. 1. ... 0. 0. 0.]
Word: %, One-Hot Encoding: [0. 0. 0. ... 0. 0. 0.]
Word: &, One-Hot Encoding: [0. 0. 0. ... 0. 0. 0.]
Word: ', One-Hot Encoding: [0. 0. 0. ... 0. 0. 0.]
Word: '', One-Hot Encoding: [0. 0. 0. ... 0. 0. 0.]
Word: '., One-Hot Encoding: [0. 0. 0. ... 0. 0. 0.]
Word: '01, One-Hot Encoding: [0. 0. 0. ... 0. 0. 0.]
Word: '02, One-Hot Encoding: [0. 0. 0. ... 0. 0. 0.]
Word: '03, One-Hot Encoding: [0. 0. 0. ... 0. 0. 0.]
Word: '04, One-Hot Encoding: [0. 0. 0. ... 0. 0. 0.]
Word: '06, One-Hot Encoding: [0. 0. 0. ... 0. 0. 0.]
Word: '10, One-Hot Encoding: [0. 0. 0. ... 0. 0. 0.]
Word: '12, One-Hot Encoding: [0. 0. 0. ... 0. 0. 0.]
Word: '2001, One-Hot Encoding: [0. 0. 0. ... 0. 0. 0.]
Word: '20s, One-Hot Encoding: [0. 0. 0. ... 0. 0. 0.]
Word: '24, One-Hot Encoding: [0. 0. 0. ... 0. 0. 0.]
Word: '30, One-Hot Encoding: [0. 0. 0. ... 0. 0. 0.]
Word

Bag of Word/ Count Vectorizer

In [ ]:
vectorizer = CountVectorizer() # Initialize CountVectorizer
X = vectorizer.fit_transform(common_words) # Vectorize the common words

print(X.toarray())
print(vectorizer.get_feature_names_out())

[[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 ...
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]]
['00' '000' '007' ... 'émigré' 'émigrés' 'über']


Term Frequency-Inverse Document Frequency (TF-IDF)

In [ ]:
tfidf_vectorizer = TfidfVectorizer() # Initialize TfidfVectorizer
X_tfidf = tfidf_vectorizer.fit_transform(common_words) # TF-IDF vectorize the common words


print(X_tfidf.toarray())
print(tfidf_vectorizer.get_feature_names_out())

[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]
['00' '000' '007' ... 'émigré' 'émigrés' 'über']
